In [60]:
torch.LongTensor([1,2,3]).unsqueeze(1)

tensor([[1],
        [2],
        [3]])

In [79]:
import sys
sys.path.append("../src/")
import os
import time
import json
import torch
import random
import datetime
import pickle as pkl
import torch.nn as nn
from types import NoneType
from itertools import cycle
import torch.optim as optim
from utils import get_next_batch
from vocabulary import Vocabulary
from pytorch_lightning import Trainer
from typing import Union, Mapping, Any
from pytorch_lightning import LightningModule
from pytorch_lightning.loggers import CSVLogger
from pytorch_lightning.callbacks import EarlyStopping
from torch.utils.data import Dataset, IterableDataset
from torch.utils.data import DataLoader, RandomSampler
from pytorch_lightning.callbacks import ModelCheckpoint


DEBUG = False
BATCH_SIZE = 256
EPOCHS = 10
# FNAME, _ = os.path.splitext(os.path.basename(__file__))

FNAME = "w06"

def log(msg: str):
    now = datetime.datetime.now()
    dttm = now.strftime(format="%Y-%m-%d %H:%M:%S.%f") 
    print(f"[{dttm}] {msg}")


def get_samples(tokenized_texts, window_size, texts_count):
    for text_num, tokens in enumerate(tokenized_texts):
        if texts_count and text_num >= texts_count:
            break
        for i in range(len(tokens)):
            central_word = torch.LongTensor(
                [vocabulary.get_index(tokens[i])]
            )
            context = torch.LongTensor(
                [
                    vocabulary.get_index(tokens[i + delta])
                    for delta in range(-window_size, window_size + 1)
                    if 0 <= (i + delta) < len(tokens)
                ]
            )
            # print(
            #     f"{tokens[i]=} {vocabulary.get_index(tokens[i])=} "
            #     f"{torch.LongTensor(vocabulary.get_index(tokens[i]))} "
            #     f"{central_word=} {context=}"
            # )
            # print(f"{central_word} {context}")
            if 2*window_size == context.shape[0]:
                yield central_word, context


def get_samples_cycle(tokenized_texts, window_size, texts_count):
    while True:
        for sample in get_samples(tokenized_texts, window_size, texts_count):
            yield sample


class Word2VecDataset(Dataset):
    def __init__(self, tokenized_texts, vocabulary, window_size=2, texts_count=100000):
        self.samples = list(get_samples(tokenized_texts, window_size, texts_count))
    
    def __len__(self):
        return len(self.samples)
    
    def __getitem__(self, index):
        return self.samples[index]


class Word2VecIterableDataset(IterableDataset):
    def __init__(self, tokenized_texts, vocabulary, window_size=2, texts_count=None):
        self.tokenized_texts = tokenized_texts
        self.vocabulary = vocabulary
        self.window_size = window_size
        self.texts_count = texts_count

    def __iter__(self):
        return get_samples_cycle(self.tokenized_texts, self.window_size, self.texts_count)


class SkipGramModel(LightningModule):
    def __init__(self, vocab_size, embedding_dim=128):
        super().__init__()
        self.embeddings = nn.Embedding(vocab_size, embedding_dim)
        self.out_layer = nn.Linear(embedding_dim, vocab_size)
        self.loss = nn.CrossEntropyLoss()
        self.train_outputs = []
        self.val_outputs = []
        self.test_outputs = []
    
    def forward(self, centrals, contexts):
        projections = self.embeddings.forward(contexts).sum(axis=1)
        # print(f"{projections.shape=}")
        logits = self.out_layer.forward(projections)
        # logits = logits.transpose(1, 2)
        # logits = logits.unsqueeze(1)
        # print(f"{logits.shape=} {centrals.shape=}")
        loss = self.loss(logits, centrals.squeeze())
        return loss
    
    def training_step(self, batch, batch_nb):
        result = self(*batch)
        self.log("loss", result)
        return {'loss': result}
    
    def validation_step(self, batch, batch_nb):
        result = self(*batch)
        self.log("val_loss", result)  
        return {'val_loss': result}

    def test_step(self, batch, batch_nb):
        result = self(*batch)
        self.log("test_loss", result)
        return {'test_loss': self(*batch)}

    def on_train_batch_end(
        self,
        outputs: Union[torch.Tensor, Mapping[str, Any], NoneType],
        batch: Any,
        batch_idx: int,
        dataloader_idx: int = 0,
    ) -> None:
        self.train_outputs.append(outputs)
    
    def on_train_epoch_end(self):
        outputs = self.train_outputs
        avg_loss = torch.stack([x['loss'] for x in outputs]).mean()
        tensorboard_logs = {'loss': avg_loss}
        self.log("train_loss_epoch", avg_loss, on_step=False, on_epoch=True)
        return {'train_loss_epoch': avg_loss, 'progress_bar': tensorboard_logs}
    
    def on_validation_batch_end(
        self,
        outputs: Union[torch.Tensor, Mapping[str, Any], NoneType],
        batch: Any,
        batch_idx: int,
        dataloader_idx: int = 0,
    ) -> None:
        self.val_outputs.append(outputs)
    
    def on_validation_epoch_end(self):
        outputs = self.val_outputs
        avg_loss = torch.stack([x['val_loss'] for x in outputs]).mean()
        tensorboard_logs = {'val_loss': avg_loss}
        self.log("val_loss_epoch", avg_loss, on_step=False, on_epoch=True)
        return {'val_loss_epoch': avg_loss, 'progress_bar': tensorboard_logs}

    def on_test_batch_end(
        self,
        outputs: Union[torch.Tensor, Mapping[str, Any], NoneType],
        batch: Any,
        batch_idx: int,
        dataloader_idx: int = 0,
    ) -> None:
        self.test_outputs.append(outputs)
    
    def on_test_epoch_end(self):
        outputs = self.test_outputs 
        avg_loss = torch.stack([x['test_loss'] for x in outputs]).mean()
        tensorboard_logs = {'test_loss': avg_loss}
        self.log("test_loss_epoch", avg_loss, on_step=False, on_epoch=True)
        return {'test_loss_epoch': avg_loss, 'progress_bar': tensorboard_logs}
    
    def configure_optimizers(self):
        optimizer = torch.optim.Adam(self.parameters(), lr=1e-4)
        return [optimizer]



In [5]:
log("BEGIN")
log("loading prepared data...")
with open("../data/prepared.pkl", "rb") as fp:
    prepared = pkl.load(fp)
vocabulary = prepared["vocabulary"]
texts = prepared["texts"]
contexts = prepared["contexts"]
test_texts = prepared["test_texts"]
del prepared
log("data loaded")


[2024-03-31 17:58:04.529524] BEGIN
[2024-03-31 17:58:04.529610] loading prepared data...
[2024-03-31 17:58:23.228757] data loaded


In [55]:
train_data = Word2VecIterableDataset(texts, vocabulary)
train_loader = DataLoader(train_data, batch_size=BATCH_SIZE)
for i, data in enumerate(train_loader):
    print(data[0].shape, data[1].shape)
    if 5<i:
        break

torch.Size([256, 1]) torch.Size([256, 4])
torch.Size([256, 1]) torch.Size([256, 4])
torch.Size([256, 1]) torch.Size([256, 4])
torch.Size([256, 1]) torch.Size([256, 4])
torch.Size([256, 1]) torch.Size([256, 4])
torch.Size([256, 1]) torch.Size([256, 4])
torch.Size([256, 1]) torch.Size([256, 4])


In [16]:
data.shape

torch.Size([579])

In [ ]:
random.shuffle(texts)
train_data = Word2VecIterableDataset(texts, vocabulary)
train_loader = DataLoader(train_data, batch_size=BATCH_SIZE)
random.shuffle(test_texts)
val_data = Word2VecIterableDataset(test_texts, vocabulary)
val_loader = DataLoader(val_data, batch_size=BATCH_SIZE)
model = SkipGramModel(vocabulary.size)
early_stop_callback = EarlyStopping(
    monitor="val_loss",
    min_delta=0.0,
    patience=5,
    verbose=True,
    mode="min",
)
ckpt_callback = ModelCheckpoint(
    monitor="val_loss",
    dirpath="ckpt",
    filename=f"{FNAME}-{{epoch}}-{{val_loss:.2f}}",
    save_top_k=3,
    mode="min",
    save_last=True
)
trainer = Trainer(
    max_epochs=EPOCHS,
    callbacks=[early_stop_callback, ckpt_callback],
    limit_train_batches=2 if DEBUG else 40000,
    limit_val_batches=2 if DEBUG else 500,
    val_check_interval=1 if DEBUG else 2000,
    # enable_progress_bar=False,
)
log("training...")
trainer.fit(model, train_loader, val_loader)
log("END")

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs

  | Name       | Type             | Params
------------------------------------------------
0 | embeddings | Embedding        | 9.1 M 
1 | out_layer  | Linear           | 9.2 M 
2 | loss       | CrossEntropyLoss | 0     
------------------------------------------------
18.3 M    Trainable params
0         Non-trainable params
18.3 M    Total params
73.179    Total estimated model params size (MB)


[2024-03-31 19:55:50.403495] training...
Epoch 0:   5%|██▉                                                        | 2000/40000 [03:09<1:00:02, 10.55it/s, v_num=39]
Validation: |                                                                                       | 0/? [00:00<?, ?it/s]
Validation DataLoader 0: 100%|██████████████████████████████████████████████████████████| 500/500 [00:20<00:00, 24.32it/s]

Metric val_loss improved. New best score: 6.210



Epoch 0:  10%|█████▉                                                     | 4000/40000 [06:45<1:00:46,  9.87it/s, v_num=39]
Validation: |                                                                                       | 0/? [00:00<?, ?it/s]
Validation DataLoader 0: 100%|██████████████████████████████████████████████████████████| 500/500 [00:20<00:00, 24.48it/s]

Metric val_loss improved by 1.222 >= min_delta = 0.0. New best score: 4.988


...


Epoch 2:  45%|███████████████████████████                                 | 18000/40000 [33:18<40:42,  9.01it/s, v_num=39]
Validation: |                                                                                       | 0/? [00:00<?, ?it/s]
Validation DataLoader 0: 100%|██████████████████████████████████████████████████████████| 500/500 [00:21<00:00, 23.67it/s]

Metric val_loss improved by 0.008 >= min_delta = 0.0. New best score: 1.758



Epoch 2:  50%|██████████████████████████████                              | 20000/40000 [37:04<37:04,  8.99it/s, v_num=39]
Validation: |                                                                                       | 0/? [00:00<?, ?it/s]
Validation DataLoader 0: 100%|██████████████████████████████████████████████████████████| 500/500 [00:21<00:00, 23.74it/s]

Metric val_loss improved by 0.003 >= min_delta = 0.0. New best score: 1.755



Epoch 2:  55%|█████████████████████████████████                           | 22000/40000 [40:50<33:24,  8.98it/s, v_num=39]
Validation: |                                                                                       | 0/? [00:00<?, ?it/s]
Validation DataLoader 0:  92%|█████████████████████████████████████████████████████▏    | 459/500 [00:19<00:01, 23.53it/s]

In [25]:
for x in get_samples(texts, window_size=2, texts_count=7):
    break

In [29]:
x[0].shape

torch.Size([21])

In [28]:
x[1]

tensor([  21, 8642,    3])

In [34]:
vocabulary.get_index("для")

21

In [77]:
DEBUG

False

In [78]:
Trainer?

Init signature:
Trainer(
    *,
    accelerator: Union[str, pytorch_lightning.accelerators.accelerator.Accelerator] = 'auto',
    strategy: Union[str, pytorch_lightning.strategies.strategy.Strategy] = 'auto',
    devices: Union[List[int], str, int] = 'auto',
    num_nodes: int = 1,
    precision: Union[Literal[64, 32, 16], Literal['transformer-engine', 'transformer-engine-float16', '16-true', '16-mixed', 'bf16-true', 'bf16-mixed', '32-true', '64-true'], Literal['64', '32', '16', 'bf16'], NoneType] = None,
    logger: Union[pytorch_lightning.loggers.logger.Logger, Iterable[pytorch_lightning.loggers.logger.Logger], bool, NoneType] = None,
    callbacks: Union[List[pytorch_lightning.callbacks.callback.Callback], pytorch_lightning.callbacks.callback.Callback, NoneType] = None,
    fast_dev_run: Union[int, bool] = False,
    max_epochs: Optional[int] = None,
    min_epochs: Optional[int] = None,
    max_steps: int = -1,
    min_steps: Optional[int] = None,
    max_time: Union[str, datetime.